# Setup

In [34]:
from huggingface_hub import InferenceClient, login

In [35]:
login()

In [ ]:
from huggingface_hub import HfApi
api = HfApi()
api.upload_file(
    path_or_fileobj="baseline.ipynb",
    path_in_repo="baseline.ipynb",
    repo_id="arabic-translation-prompt-engineering/atpe-notebooks",
    repo_type="dataset",
)

<div class="alert alert-danger" role="alert" style="display: flex; align-items: center;">
    <div style="text-align: center; padding-right: 10px;">
        <i class="fa fa-exclamation-triangle fa-2x"></i>
    </div>
    <div style="display: flex; align-items: center; margin-top: 4px;"> <!-- Added margin-top to lower the text -->
        <strong>Warning: You will need to point to a model/deployment that is running.</strong>
    </div>
</div>


In [36]:
MODEL = "CohereForAI/c4ai-command-r-plus"
client = InferenceClient(MODEL)

# Translation

## Baseline

For our baseline we will translate with a simple system prompt and instruction.

### Analysis

### System Prompt
This is a pretty basic system prompt. We give a role, and an assumed understanding. We also push for goals like "highly motivated and detail-oriented". 

> You are a skilled translator with extensive experience in English to Arabic translations. You possess a deep understanding of the linguistic, cultural, and contextual nuances essential for accurate and effective translation between these languages. Highly motivated and detail-oriented, you are committed to delivering translations that maintain the integrity and intent of the original text. Your role is crucial in ensuring clear and precise communication in our multilingual system.

In [ ]:
system_prompt = """You are a skilled translator with extensive experience in English to Arabic translations. You possess a deep understanding of the linguistic, cultural, and contextual nuances essential for accurate and effective translation between these languages. Highly motivated and detail-oriented, you are committed to delivering translations that maintain the integrity and intent of the original text. Your role is crucial in ensuring clear and precise communication in our multilingual system."""

### Prompt
> Translate this from english to arabic: {en_input}.
>
> Translation: 

Again we use a simple prompt to get a translation.

In [53]:
def baseline_chat_completion(system_prompt, en_input):
    """
    Generates a completion for a chat conversation using a specified system prompt and a user input.
    """
    messages = [
        {"role": "system", "content": system_prompt},
        {"role": "user", "content": f"Translate this from english to arabic: {en_input}.\nTranslation: "},
    ]
    return client.chat_completion(messages, max_tokens=10_000)

In [50]:
en_input = "Float like a butterfly sting like a bee – his hands can’t hit what his eyes can’t see."
response = baseline_chat_completion(system_prompt, "Float like a butterfly sting like a bee – his hands can’t hit what his eyes can’t see.")

120

### Token Cost
Here we can see that the cost is quite cheap, only 92 tokens!

In [52]:
response.usage.prompt_tokens

120

In [51]:
response.choices[0].message.content

'يرفرف مثل الفراشة ويلسع كالنحلة - يديه لا يمكن أن تصيب ما لا تستطيع عينيه رؤيته.'

## Purpose Driven Translation

[](https://arxiv.org/pdf/2308.01391)